<h1 align="center">Machine learning-based prediction of early recurrence in glioblastoma patients: a glance towards precision medicine <br><br>[Null-classifier]</h1>

<h2>[1] Library</h2>

In [1]:
# OS library
import os
import sys
import argparse
import itertools
import random

# Analysis
import numpy as np
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt

# Sklearn
from boruta import BorutaPy
from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import confusion_matrix, f1_score, recall_score, classification_report, accuracy_score, auc, roc_curve
from sklearn.model_selection import RandomizedSearchCV
from sklearn.dummy import DummyClassifier

import scikitplot as skplt
from imblearn.over_sampling import RandomOverSampler, SMOTENC, SMOTE

/Users/valerio_mc/opt/anaconda3/lib/python3.7/site-packages/sklearn/utils/deprecation.py:144: FutureWarning: The sklearn.neighbors.base module is  deprecated in version 0.22 and will be removed in version 0.24. The corresponding classes / functions should instead be imported from sklearn.neighbors. Anything that cannot be imported from sklearn.neighbors is now part of the private API.
  warnings.warn(message, FutureWarning)
/Users/valerio_mc/opt/anaconda3/lib/python3.7/site-packages/sklearn/utils/deprecation.py:144: FutureWarning: The sklearn.ensemble.bagging module is  deprecated in version 0.22 and will be removed in version 0.24. The corresponding classes / functions should instead be imported from sklearn.ensemble. Anything that cannot be imported from sklearn.ensemble is now part of the private API.
  warnings.warn(message, FutureWarning)
/Users/valerio_mc/opt/anaconda3/lib/python3.7/site-packages/sklearn/utils/deprecation.py:144: FutureWarning: The sklearn.ensemble.base module is

<h2>[2] Exploratory data analysis and Data Preprocessing</h2>

<h4>[-] Load the database</h4>

In [ ]:
file = os.path.join(sys.path[0], "db.xlsx")
db = pd.read_excel(file)

print("N° of patients: {}".format(len(db)))
print("N° of columns: {}".format(db.shape[1]))
db.head()

<h4>[-] Drop unwanted columns + create <i>'results'</i> column</h4>

In [ ]:
df = db.drop(['Name_Surname','...'], axis = 'columns')

print("Effective features to consider: {} ".format(len(df.columns)-1))
print("Creating 'result' column...")

# 0 = No relapse
df.loc[df['PFS'] > 6, 'result'] = 0

# 1 = Early relapse (within 6 months)
df.loc[df['PFS'] <= 6, 'result'] = 1

df.head()

<h4>[-] Check for class imbalance in the <i>'results'</i> column </h4>

In [ ]:
print("PFS Overview")
print(df.result.value_counts())

df.result.value_counts().plot(kind='pie', autopct='%1.0f%%', colors=['skyblue', 'orange'], explode=(0.05, 0.05))

<h4>[-] Label encoding of the categorical variables </h4>

In [ ]:
df['sex'] =df['sex'].astype('category')
df['ceus'] =df['ceus'].astype('category')
df['ala'] =df['ala'].astype('category')

#df['Ki67'] =df['Ki67'].astype(int)
df['MGMT'] =df['MGMT'].astype('category')
df['IDH1'] =df['IDH1'].astype('category')

df['side'] =df['side'].astype('category')
df['ependima'] =df['ependima'].astype('category')
df['cc'] =df['cc'].astype('category')
df['necrotico_cistico'] =df['necrotico_cistico'].astype('category')
df['shift'] =df['shift'].astype('category')

## VARIABLE TO ONE-HOT-ENCODE
df['localization'] =df['localization'].astype(int)
df['clinica_esordio'] =df['clinica_esordio'].astype(int)
df['immediate_p_o'] =df['immediate_p_o'].astype(int)
df['onco_Protocol'] =df['onco_Protocol'].astype(int)

df['result'] =df['result'].astype(int)

dummy_v = ['localization', 'clinica_esordio', 'onco_Protocol', 'immediate_p_o']

df = pd.get_dummies(df, columns = dummy_v, prefix = dummy_v)

<h2>[3] Prediction Models</h2>

<h4> [-] Training and testing set splitting</h4>

In [5]:
target = df['result']
inputs = df.drop(['result', 'PFS'], axis = 'columns')
x_train, x_test, y_train, y_test = train_test_split(inputs['...'],target,test_size=0.20, random_state=10)

NameError: name 'df' is not defined

<h4> [-] Dummy Training </h4>

In [ ]:
dummy_train = DummyClassifier(strategy="uniform", random_state = 42)
dummy_train.fit(x_train, y_train)

score_dummy_train = dummy_train.score(x_train, y_train)
print("Dummy Train accuracy ***TRAIN***: ", round(score_dummy_train*100,2), "% \n")

y_dummy_train_predicted = dummy_train.predict(x_train)
y_dummy_train_proba = dummy_train.predict_proba(x_train)

cm_dummy_train = confusion_matrix(y_train, y_dummy_train_predicted)
print(cm_dummy_train, "\n")

false_positive_rate, true_positive_rate, thresholds = roc_curve(y_train, y_dummy_train_predicted)
roc_auc = auc(false_positive_rate, true_positive_rate)


print('1. The F-1 Score of the model {} \n '.format(round(f1_score(y_train, y_dummy_train_predicted, average = 'macro'), 2)))
print('2. The Recall Score of the model {} \n '.format(round(recall_score(y_train, y_dummy_train_predicted, average = 'macro'), 2)))
print('3. Classification report \n {} \n'.format(classification_report(y_train, y_dummy_train_predicted)))
print('3. AUC: \n {} \n'.format(roc_auc))

tn, fp, fn, tp = cm_dummy_train.ravel()

# Sensitivity, hit rate, Recall, or true positive rate
tpr = tp/(tp+fn)
print("Sensitivity (TPR): {}".format(tpr))

# Specificity or true negative rate
tnr = tn/(tn+fp)
print("Specificity (TNR): {}".format(tnr))

# Precision or positive predictive value
ppv = tp/(tp+fp)
print("Precision (PPV): {}".format(ppv))

# Negative predictive value
npv = tn/(tn+fn)
print("Negative Predictive Value (NPV): {}".format(npv))

# False positive rate
fpr = fp / (fp + tn)
print("False Positive Rate (FPV): {}".format(fpr))

tnr = tn/(tn+fp)


<h4> [-] Dummy Testing </h4>

In [ ]:
dummy_testing = DummyClassifier(strategy="uniform", random_state = 42)
dummy_testing.fit(x_test, y_test)

score_dummy_testing = dummy_testing.score(x_test, y_test)
print("Dummy Test accuracy ***TEST***: ", round(score_dummy_testing*100,2), "% \n")

y_dummy_testing_predicted = dummy_testing.predict(x_test)
y_dummy_testing_proba = dummy_testing.predict_proba(x_test)

cm_dummy_testing = confusion_matrix(y_test, y_dummy_testing_predicted)
print(cm_dummy_testing, "\n")

false_positive_rate, true_positive_rate, thresholds = roc_curve(y_test, y_dummy_testing_predicted)
roc_auc = auc(false_positive_rate, true_positive_rate)


print('1. The F-1 Score of the model {} \n '.format(round(f1_score(y_test, y_dummy_testing_predicted, average = 'macro'), 2)))
print('2. The Recall Score of the model {} \n '.format(round(recall_score(y_test, y_dummy_testing_predicted, average = 'macro'), 2)))
print('3. Classification report \n {} \n'.format(classification_report(y_test, y_dummy_testing_predicted)))
print('3. AUC: \n {} \n'.format(roc_auc))

tn, fp, fn, tp = cm_dummy_train.ravel()

# Sensitivity, hit rate, Recall, or true positive rate
tpr = tp/(tp+fn)
print("Sensitivity (TPR): {}".format(tpr))

# Specificity or true negative rate
tnr = tn/(tn+fp)
print("Specificity (TNR): {}".format(tnr))

# Precision or positive predictive value
ppv = tp/(tp+fp)
print("Precision (PPV): {}".format(ppv))

# Negative predictive value
npv = tn/(tn+fn)
print("Negative Predictive Value (NPV): {}".format(npv))

# False positive rate
fpr = fp / (fp + tn)
print("False Positive Rate (FPV): {}".format(fpr))

tnr = tn/(tn+fp)